In [1]:
from xclib.data import data_utils
import numpy as np
import time
import pickle

In [2]:
#Change this later. Make the path as command line argument
X_train = data_utils.read_sparse_file('ass3_parta_data/train_x.txt', force_header=True)
train_class = np.genfromtxt('ass3_parta_data/train_y.txt').reshape(-1, 1)

X_valid = data_utils.read_sparse_file('ass3_parta_data/valid_x.txt', force_header=True)
valid_class = np.genfromtxt('ass3_parta_data/valid_y.txt').reshape(-1, 1)

X_test = data_utils.read_sparse_file('ass3_parta_data/test_x.txt', force_header=True)
test_class = np.genfromtxt('ass3_parta_data/test_y.txt').reshape(-1, 1)

/home/ayushi/.local/lib/python3.6/site-packages/xclib-0.96-py3.6-linux-x86_64.egg/xclib/data/data_utils.py:173: UserWarning: Header mis-match from inferred shape!
  warnings.warn("Header mis-match from inferred shape!")


In [3]:
f = open('ass3_parta_data/train_x.txt') 
m,n = f.readlines()[0].rstrip("\n").split(" ")
m,n = int(m),int(n)
f.close()

In [4]:
classes = np.unique(train_class)
pos_class_ind = np.where(train_class == 1)
neg_class_ind = np.where(train_class == 0)

In [5]:
attributes = np.array(range(X_train.A.shape[1]))

### Entropy H(Y) is calculated assuming Y only has two classes - 0 and 1

###### So we use log_2 and use pos and neg_num

In [6]:
def calc_entropyY(train_data, train_class):
    pos_num = train_data[np.where(train_class == 1)[0]].shape[0]
    neg_num = train_data[np.where(train_class == 0)[0]].shape[0]
    
    if (pos_num == 0) or (neg_num == 0):
        entr = 0 #in the limit
    else:
        entr = (pos_num/(pos_num+neg_num))*np.log2((pos_num+neg_num)/pos_num) + (neg_num/(pos_num+neg_num))*np.log2((pos_num+neg_num)/neg_num)
        
    return entr

In [7]:
#Entropy of Raw data
start = time.time()
print(calc_entropyY(X_train.A, train_class))
print("time = ", time.time()-start)

0.997775157550985
time =  0.08927488327026367


#### Reduction in Error is given by H(Y|X) by using value to split at the node
H(Y|X) 

       = H(Y|X=x)P(X=x)  -- find the two splits 

       = H(Y=y|X=x)P(X=x) -- find the entropy of both the splits. 

       = calc_entropy(split1, train_class_split1).P(X=x)
    

In [8]:
def calc_red_error(train_data, split, split_class, train_class):
    #print("In reduction of Error Module")
    #print(train_data.shape[0])
    error = 0
    for i in range(len(split)):
    #    print("Split shape = ", split[i].shape)
        error += (split[i].shape[0]/train_data.shape[0])*calc_entropyY(split[i], split_class[i])
    #print("Reduction in error = ", error)
    return error


In [9]:
def find_best_attr(train_data, train_class):
    #max_mutual_info = 0;   This doesnt work for the cases when mutual info becomes negative. 
    max_mutual_info = float("-inf");
    median = (np.median(train_data, axis=0))        
    #print(median)
    for i in range(len(attributes)):
        split = []
        split_class = []
        split.append(train_data[np.where(train_data[:,i] <= median[i])])
        split.append(train_data[np.where(train_data[:,i] > median[i])])
        split_class.append(train_class[np.where(train_data[:,i] <= median[i])])
        split_class.append(train_class[np.where(train_data[:,i] > median[i])])
        mutual_info = calc_entropyY(train_data, train_class) - calc_red_error(train_data, split, split_class, train_class)
        #print(mutual_info)
        if max_mutual_info < mutual_info:
            max_mutual_info = mutual_info
            best_attr = attributes[i]
            thres = median[i]
    return max_mutual_info, best_attr, thres

In [10]:
start = time.time()
print(find_best_attr(X_train.A, train_class))
print(time.time()-start)

(0.0793751756882577, 217, 0.0)
50.35675883293152


### Every Node  in the tree will have the following contents:

1. Left Subtree
2. Right Subtree
3. Attribute Name on which this node will split
4. Threshold of the attribute for left and right subtree (Median) - int value
5. Entropy
6. Whether this node is leaf or not - True/False
7. A final value of Y=0 or Y=1 in case of leaf

In [10]:
class newNode(object):
    def __init__(self, attr, Th, value):
        self.left = None
        self.right = None
        self.attribute = attr
        self.threshold = Th
        self.value = value
        self.leaf = False
        self.final = None
        self.parent = None
    
    def find_root(self):
        while (self.parent is not None):
            self = self.parent
            self = self.find_root()
        root = self
        return root

    def calc_accuracy(self, tra_data, tra_classes, val_data, val_classes, test_data, test_classes):
        root = self.find_root()
        #print("Root found at = ", root)
        t_acc = 0; v_acc = 0; tes_acc = 0
        for i in range(len(tra_data)):
            pred = predict(root, tra_data[i])
            if (pred is None):
                continue
            if (pred == tra_classes[i]):
                t_acc+=1
        for i in range(len(val_data)):
            pred = predict(root, val_data[i])
            if (pred is None):
                continue            
            if (pred == val_classes[i]):
                v_acc += 1
        for i in range(len(test_data)):
            pred = predict(root, test_data[i])
            if (pred is None):
                continue
            if(pred == test_classes[i]):
                tes_acc+=1
        
        return t_acc/len(tra_classes), v_acc/len(val_classes), tes_acc/len(test_classes);

In [11]:
class Tree(object):
    def __init__(self):
        self.tree = None
    def buildTree(self, data, classes, parent, depth, d_thres):
        self.tree = growTree(data, classes, parent, depth, d_thres)

In [12]:
def predict(tree, data):
    if tree is None:
        return None
    if tree.leaf:
        return tree.final
    if tree.left is None and tree.right is None:
        if tree.value[0] > tree.value[1]:
            return 0
        else:
            return 1
    if data[tree.attribute] <= tree.threshold:
        return predict(tree.left, data)
    elif data[tree.attribute] > tree.threshold:
        return predict(tree.right, data)


In [13]:
def growTree(train_data, classes, parent, depth, depth_threshold):
    global num_nodes
    pos_num = train_data[np.where(classes == 1)[0]].shape[0]
    neg_num = train_data[np.where(classes == 0)[0]].shape[0]
    #print("The number of nodes present in the graph = ", num_nodes)
    #print(neg_num, pos_num)

    if (depth == depth_threshold):
        num_nodes+=1
        leaf = newNode(None, None, None)
        leaf.parent = parent
        leaf.leaf = True
        if (pos_num > neg_num):
            leaf.final = 1
        else:
            leaf.final = 0
        return leaf
            
    elif(pos_num == 0 or neg_num == 0):
        num_nodes+=1
        leaf = newNode(None, None, None)
        leaf.leaf = True
        leaf.parent = parent
        
        if(pos_num != 0):
            leaf.final = 1
        elif(neg_num != 0):
            leaf.final = 0
        return leaf
        
    else:
        mutual_info, best_attr, thresh = find_best_attr(train_data, classes)
        #print("Best Attribute with Threshold = ", best_attr, thresh)
        num_nodes+=1
        left_split = train_data[np.where(train_data[:,best_attr] <= thresh)]
        right_split = train_data[np.where(train_data[:,best_attr] > thresh)]
        left_split_class = classes[np.where(train_data[:,best_attr] <= thresh)]
        right_split_class = classes[np.where(train_data[:,best_attr] > thresh)]
        
        if (left_split.shape[0] == 0):
            leaf = newNode(None, None, None)
            leaf.parent = parent
            
            leaf.leaf = True
            pos = left_split[np.where(left_split_class == 1)[0]].shape[0]
            neg = left_split[np.where(left_split_class == 0)[0]].shape[0]
            if (pos>neg):
                leaf.final = 1
            else:
                leaf.final = 0
            return leaf
        elif (right_split.shape[0] == 0):
            leaf = newNode(None, None, None)
            leaf.leaf = True
            leaf.parent = parent
            
            pos = right_split[np.where(right_split_class == 1)[0]].shape[0]
            neg = right_split[np.where(right_split_class == 0)[0]].shape[0]
            if (pos>neg):
                leaf.final = 1
            else:
                leaf.final = 0
            return leaf
        else:
            addNode = newNode(best_attr, thresh, [neg_num, pos_num])
            addNode.parent = parent
            #print(parent)
            #print("The value of the class examples in this node = ", addNode.value)
            #print("Building left tree on =", left_split.shape[0])
            addNode.left = growTree(left_split, left_split_class, addNode, depth+1, depth_threshold)
            #print("Building right tree in = ", right_split.shape[0])
            addNode.right = growTree(right_split, right_split_class, addNode, depth+1, depth_threshold)
            return addNode

In [18]:
nodes = []
time_taken = []
train_acc=[]; val_acc= []; test_acc = []


start = time.time()
num_nodes = 0
root = Tree()
root.buildTree(X_train.A, train_class, None, 0, float("inf"))
    
#root = growTree(X_train.A, train_class, 0, 8)


In [20]:
print("Time Taken to grow tree = {} sec".format(time.time() - start))

Time Taken to grow tree = 795.9404263496399 sec


In [67]:
print(num_nodes)

19999


In [14]:
with open('tree_b.pickle', 'rb') as f:
    root = pickle.load(f)

In [15]:
train_acc, val_acc, test_acc = root.tree.calc_accuracy(X_train.A, train_class, X_valid.A, valid_class, X_test.A, test_class)

In [16]:
def printInorder(graph): 
    global n
    if graph: 
        n+=1
        # First recur on left child 
        printInorder(graph.left) 
  
        # then print the data of node 
        print(graph, graph.attribute, graph.leaf, graph.parent, graph.final), 
  
        # now recur on right child 
        printInorder(graph.right) 
  

Test Accuracy = 71.67%
Train Accuracy = 
Validation Accuracy = 

In [18]:
n = 0
printInorder(root.tree)
print(n)

<__main__.newNode object at 0x7f2b320628d0> None True <__main__.newNode object at 0x7f2b32062160> 0
<__main__.newNode object at 0x7f2b32062160> 22 False <__main__.newNode object at 0x7f2b320620f0> None
<__main__.newNode object at 0x7f2b32062860> None True <__main__.newNode object at 0x7f2b32062160> 1
<__main__.newNode object at 0x7f2b320620f0> 104 False <__main__.newNode object at 0x7f2b32062080> None
<__main__.newNode object at 0x7f2b320627b8> None True <__main__.newNode object at 0x7f2b320620f0> 0
<__main__.newNode object at 0x7f2b32062080> 20 False <__main__.newNode object at 0x7f2b32062048> None
<__main__.newNode object at 0x7f2b32062320> None True <__main__.newNode object at 0x7f2b320622e8> 1
<__main__.newNode object at 0x7f2b320622e8> 20 False <__main__.newNode object at 0x7f2b32062080> None
<__main__.newNode object at 0x7f2b32062940> None True <__main__.newNode object at 0x7f2b32062128> 0
<__main__.newNode object at 0x7f2b32062128> 20 False <__main__.newNode object at 0x7f2b3206

<__main__.newNode object at 0x7f2b32299518> None True <__main__.newNode object at 0x7f2b32299438> 0
<__main__.newNode object at 0x7f2b322992b0> 36 False <__main__.newNode object at 0x7f2b32042ef0> None
<__main__.newNode object at 0x7f2b32299588> None True <__main__.newNode object at 0x7f2b32299550> 0
<__main__.newNode object at 0x7f2b32299550> 36 False <__main__.newNode object at 0x7f2b322992b0> None
<__main__.newNode object at 0x7f2b32299630> None True <__main__.newNode object at 0x7f2b322995f8> 0
<__main__.newNode object at 0x7f2b322995f8> 36 False <__main__.newNode object at 0x7f2b322995c0> None
<__main__.newNode object at 0x7f2b32299668> None True <__main__.newNode object at 0x7f2b322995f8> 1
<__main__.newNode object at 0x7f2b322995c0> 36 False <__main__.newNode object at 0x7f2b32299550> None
<__main__.newNode object at 0x7f2b322996a0> None True <__main__.newNode object at 0x7f2b322995c0> 0
<__main__.newNode object at 0x7f2b32042eb8> 107 False <__main__.newNode object at 0x7f2b3204

<__main__.newNode object at 0x7f2b3234d400> None True <__main__.newNode object at 0x7f2b3234d0f0> 1
<__main__.newNode object at 0x7f2b3234d0b8> 209 False <__main__.newNode object at 0x7f2b323b0c18> None
<__main__.newNode object at 0x7f2b3234d470> None True <__main__.newNode object at 0x7f2b3234d438> 0
<__main__.newNode object at 0x7f2b3234d438> 151 False <__main__.newNode object at 0x7f2b3234d0b8> None
<__main__.newNode object at 0x7f2b3234d4a8> None True <__main__.newNode object at 0x7f2b3234d438> 1
<__main__.newNode object at 0x7f2b323b02b0> 114 False <__main__.newNode object at 0x7f2b323b0278> None
<__main__.newNode object at 0x7f2b3234d4e0> None True <__main__.newNode object at 0x7f2b323b02b0> 0
<__main__.newNode object at 0x7f2b323b0278> 209 False <__main__.newNode object at 0x7f2b323b0240> None
<__main__.newNode object at 0x7f2b3234d710> None True <__main__.newNode object at 0x7f2b3234d6d8> 0
<__main__.newNode object at 0x7f2b3234d6d8> 20 False <__main__.newNode object at 0x7f2b3

<__main__.newNode object at 0x7f2b322278d0> None True <__main__.newNode object at 0x7f2b32227860> 0
<__main__.newNode object at 0x7f2b32213f28> 210 False <__main__.newNode object at 0x7f2b32213ef0> None
<__main__.newNode object at 0x7f2b32227940> None True <__main__.newNode object at 0x7f2b32227908> 1
<__main__.newNode object at 0x7f2b32227908> 141 False <__main__.newNode object at 0x7f2b32213f28> None
<__main__.newNode object at 0x7f2b322279b0> None True <__main__.newNode object at 0x7f2b32227978> 1
<__main__.newNode object at 0x7f2b32227978> 210 False <__main__.newNode object at 0x7f2b32227908> None
<__main__.newNode object at 0x7f2b322279e8> None True <__main__.newNode object at 0x7f2b32227978> 0
<__main__.newNode object at 0x7f2b32213ef0> 121 False <__main__.newNode object at 0x7f2b320626a0> None
<__main__.newNode object at 0x7f2b32227e48> None True <__main__.newNode object at 0x7f2b32227e10> 0
<__main__.newNode object at 0x7f2b32227e10> 19 False <__main__.newNode object at 0x7f2b3

<__main__.newNode object at 0x7f2b3208f278> None True <__main__.newNode object at 0x7f2b3208f240> 0
<__main__.newNode object at 0x7f2b3208f240> 20 False <__main__.newNode object at 0x7f2b3208f208> None
<__main__.newNode object at 0x7f2b3208f2b0> None True <__main__.newNode object at 0x7f2b3208f240> 1
<__main__.newNode object at 0x7f2b3208f208> 80 False <__main__.newNode object at 0x7f2b3208f1d0> None
<__main__.newNode object at 0x7f2b3208f2e8> None True <__main__.newNode object at 0x7f2b3208f208> 1
<__main__.newNode object at 0x7f2b3208f1d0> 80 False <__main__.newNode object at 0x7f2b3208f198> None
<__main__.newNode object at 0x7f2b3208f358> None True <__main__.newNode object at 0x7f2b3208f320> 1
<__main__.newNode object at 0x7f2b3208f320> 80 False <__main__.newNode object at 0x7f2b3208f1d0> None
<__main__.newNode object at 0x7f2b3208f390> None True <__main__.newNode object at 0x7f2b3208f320> 0
<__main__.newNode object at 0x7f2b3208f198> 80 False <__main__.newNode object at 0x7f2b3208f

...

<__main__.newNode object at 0x7f2b314b9438> 52 False <__main__.newNode object at 0x7f2b314b9400> None
<__main__.newNode object at 0x7f2b314b9cc0> None True <__main__.newNode object at 0x7f2b314b9c88> 0
<__main__.newNode object at 0x7f2b314b9c88> 83 False <__main__.newNode object at 0x7f2b314b9438> None
<__main__.newNode object at 0x7f2b314b9cf8> None True <__main__.newNode object at 0x7f2b314b9c88> 1
<__main__.newNode object at 0x7f2b314b9400> 87 False <__main__.newNode object at 0x7f2b31496cc0> None
<__main__.newNode object at 0x7f2b314b9eb8> None True <__main__.newNode object at 0x7f2b314b9e80> 0
<__main__.newNode object at 0x7f2b314b9e80> 151 False <__main__.newNode object at 0x7f2b314b9e48> None
<__main__.newNode object at 0x7f2b314b9ef0> None True <__main__.newNode object at 0x7f2b314b9e80> 0
<__main__.newNode object at 0x7f2b314b9e48> 209 False <__main__.newNode object at 0x7f2b314b9e10> None
<__main__.newNode object at 0x7f2b314b9f28> None True <__main__.newNode object at 0x7f2b

<__main__.newNode object at 0x7f2b313b49b0> 64 False <__main__.newNode object at 0x7f2b313b4978> None
<__main__.newNode object at 0x7f2b313b4a20> None True <__main__.newNode object at 0x7f2b313b49b0> 0
<__main__.newNode object at 0x7f2b313b4978> 193 False <__main__.newNode object at 0x7f2b313b4940> None
<__main__.newNode object at 0x7f2b313b4a58> None True <__main__.newNode object at 0x7f2b313b4978> 0
<__main__.newNode object at 0x7f2b313b4940> 15 False <__main__.newNode object at 0x7f2b313b4908> None
<__main__.newNode object at 0x7f2b313b4a90> None True <__main__.newNode object at 0x7f2b313b4940> 0
<__main__.newNode object at 0x7f2b313b4908> 79 False <__main__.newNode object at 0x7f2b313b48d0> None
<__main__.newNode object at 0x7f2b313b4ac8> None True <__main__.newNode object at 0x7f2b313b4908> 1
<__main__.newNode object at 0x7f2b313b48d0> 52 False <__main__.newNode object at 0x7f2b3160e8d0> None
<__main__.newNode object at 0x7f2b313b4b38> None True <__main__.newNode object at 0x7f2b3

<__main__.newNode object at 0x7f2b312aea90> None True <__main__.newNode object at 0x7f2b312ae8d0> 1
<__main__.newNode object at 0x7f2b3129f0b8> 234 False <__main__.newNode object at 0x7f2b3129f080> None
<__main__.newNode object at 0x7f2b312aeac8> None True <__main__.newNode object at 0x7f2b3129f0b8> 0
<__main__.newNode object at 0x7f2b3129f080> 201 False <__main__.newNode object at 0x7f2b3129f048> None
<__main__.newNode object at 0x7f2b312aeb00> None True <__main__.newNode object at 0x7f2b3129f080> 0
<__main__.newNode object at 0x7f2b3129f048> 363 False <__main__.newNode object at 0x7f2b3128efd0> None
<__main__.newNode object at 0x7f2b312aeb38> None True <__main__.newNode object at 0x7f2b3129f048> 0
<__main__.newNode object at 0x7f2b3128efd0> 193 False <__main__.newNode object at 0x7f2b3128ef98> None
<__main__.newNode object at 0x7f2b312aee80> None True <__main__.newNode object at 0x7f2b312aee48> 0
<__main__.newNode object at 0x7f2b312aee48> 19 False <__main__.newNode object at 0x7f2b3

<__main__.newNode object at 0x7f2b311ad630> None True <__main__.newNode object at 0x7f2b311ad5c0> 0
<__main__.newNode object at 0x7f2b311ad588> 19 False <__main__.newNode object at 0x7f2b311ad518> None
<__main__.newNode object at 0x7f2b311ad668> None True <__main__.newNode object at 0x7f2b311ad588> 0
<__main__.newNode object at 0x7f2b311ad320> 93 False <__main__.newNode object at 0x7f2b311ad2e8> None
<__main__.newNode object at 0x7f2b311ad748> None True <__main__.newNode object at 0x7f2b311ad710> 1
<__main__.newNode object at 0x7f2b311ad710> 20 False <__main__.newNode object at 0x7f2b311ad6d8> None
<__main__.newNode object at 0x7f2b311ad7b8> None True <__main__.newNode object at 0x7f2b311ad780> 0
<__main__.newNode object at 0x7f2b311ad780> 20 False <__main__.newNode object at 0x7f2b311ad710> None
<__main__.newNode object at 0x7f2b311ad7f0> None True <__main__.newNode object at 0x7f2b311ad780> 1
<__main__.newNode object at 0x7f2b311ad6d8> 19 False <__main__.newNode object at 0x7f2b311ad

<__main__.newNode object at 0x7f2b310a8470> None True <__main__.newNode object at 0x7f2b310a8400> 0
<__main__.newNode object at 0x7f2b310a83c8> 15 False <__main__.newNode object at 0x7f2b310a8390> None
<__main__.newNode object at 0x7f2b310a84a8> None True <__main__.newNode object at 0x7f2b310a83c8> 0
<__main__.newNode object at 0x7f2b310a8390> 115 False <__main__.newNode object at 0x7f2b310a8358> None
<__main__.newNode object at 0x7f2b310a84e0> None True <__main__.newNode object at 0x7f2b310a8390> 1
<__main__.newNode object at 0x7f2b310a8358> 245 False <__main__.newNode object at 0x7f2b310a8128> None
<__main__.newNode object at 0x7f2b310a8518> None True <__main__.newNode object at 0x7f2b310a8358> 0
<__main__.newNode object at 0x7f2b310a80f0> 375 False <__main__.newNode object at 0x7f2b310a80b8> None
<__main__.newNode object at 0x7f2b310a8588> None True <__main__.newNode object at 0x7f2b310a8550> 1
<__main__.newNode object at 0x7f2b310a8550> 9 False <__main__.newNode object at 0x7f2b310

In [19]:
print("--------------Original Tree------------------------------\n")
print("Number of Nodes = ", n)
print("The Training Accuracy on Full-Grown Tree is = {:2.3f}%".format(train_acc*100))
print("The Vaidation Accuracy on Full-Grown Tree is = {:2.3f}%".format(val_acc*100))
print("The Test Accuracy on Full-Grown Tree is = {:2.3f}%".format(test_acc*100))

--------------Original Tree------------------------------

Number of Nodes =  19999
The Training Accuracy on Full-Grown Tree is = 83.875%
The Vaidation Accuracy on Full-Grown Tree is = 71.885%
The Test Accuracy on Full-Grown Tree is = 71.675%


In [24]:
with open('tree_b.pickle', 'rb') as f:
    root = pickle.load(f)

# Post Pruning the tree by removing all the Leaf Nodes

In [27]:
def prune(rootT): 
    #print(rootT.attribute)
    if rootT.attribute is None:
        return rootT
      
    if rootT.left.leaf == True and rootT.right.leaf == True:
        #print("Leaf", rootT.value)
        new_root = rootT
        new_root.leaf = True
        new_root.final = [1 if rootT.value[0]<rootT.value[1] else 0][0]
        temp = rootT
        rootT.left = None
        rootT.right = None
        rootT = None
        
        del(temp)
        #print("retunring", new_root.attribute, new_root.final)
        return new_root

    rootT.left = prune(rootT.left) 
        
    rootT.right = prune(rootT.right)

    return rootT

In [28]:
prune(root.tree)


In [29]:
n = 0
printInorder(root.tree)
print(n)

<__main__.newNode object at 0x7f2b2dbbc828> 104 True <__main__.newNode object at 0x7f2b2dbbc550> 1
<__main__.newNode object at 0x7f2b2dbbc550> 20 False <__main__.newNode object at 0x7f2b2dbbcef0> None
<__main__.newNode object at 0x7f2b320622b0> None True <__main__.newNode object at 0x7f2b320627f0> 1
<__main__.newNode object at 0x7f2b320627f0> 20 False <__main__.newNode object at 0x7f2b2dbbc550> None
<__main__.newNode object at 0x7f2b3101aeb8> 20 True <__main__.newNode object at 0x7f2b70359eb8> 0
<__main__.newNode object at 0x7f2b70359eb8> 20 False <__main__.newNode object at 0x7f2b320627f0> None
<__main__.newNode object at 0x7f2b3101a588> None True <__main__.newNode object at 0x7f2b70359eb8> 1
<__main__.newNode object at 0x7f2b2dbbcef0> 32 False <__main__.newNode object at 0x7f2b2dbbcf60> None
<__main__.newNode object at 0x7f2b3101a978> None True <__main__.newNode object at 0x7f2b2dbbcef0> 0
<__main__.newNode object at 0x7f2b2dbbcf60> 36 False <__main__.newNode object at 0x7f2b2dbbcfd0

<__main__.newNode object at 0x7f2b31060400> 34 True <__main__.newNode object at 0x7f2b322bf4a8> 0
<__main__.newNode object at 0x7f2b32046080> 119 False <__main__.newNode object at 0x7f2b320463c8> None
<__main__.newNode object at 0x7f2b310600b8> 100 True <__main__.newNode object at 0x7f2b31060240> 0
<__main__.newNode object at 0x7f2b31060240> 100 False <__main__.newNode object at 0x7f2b310600f0> None
<__main__.newNode object at 0x7f2b31060048> None True <__main__.newNode object at 0x7f2b31060080> 0
<__main__.newNode object at 0x7f2b31060080> 100 False <__main__.newNode object at 0x7f2b31060240> None
<__main__.newNode object at 0x7f2b70359860> None True <__main__.newNode object at 0x7f2b716b42e8> 0
<__main__.newNode object at 0x7f2b716b42e8> 100 False <__main__.newNode object at 0x7f2b31060080> None
<__main__.newNode object at 0x7f2b70359da0> 100 True <__main__.newNode object at 0x7f2b716b42e8> 0
<__main__.newNode object at 0x7f2b310600f0> 100 False <__main__.newNode object at 0x7f2b3106

<__main__.newNode object at 0x7f2b2e1cdb00> None True <__main__.newNode object at 0x7f2b2e1cd9b0> 1
<__main__.newNode object at 0x7f2b2e1cd978> 19 False <__main__.newNode object at 0x7f2b2e1cd748> None
<__main__.newNode object at 0x7f2b2e1cdb38> None True <__main__.newNode object at 0x7f2b2e1cd978> 0
<__main__.newNode object at 0x7f2b2e1cd710> 245 False <__main__.newNode object at 0x7f2b2e1cd6d8> None
<__main__.newNode object at 0x7f2b2e1cdc18> 106 True <__main__.newNode object at 0x7f2b2e1cdbe0> 1
<__main__.newNode object at 0x7f2b2e1cdbe0> 36 False <__main__.newNode object at 0x7f2b2e1cdba8> None
<__main__.newNode object at 0x7f2b2e1cdcc0> None True <__main__.newNode object at 0x7f2b2e1cdbe0> 0
<__main__.newNode object at 0x7f2b2e1cdba8> 20 False <__main__.newNode object at 0x7f2b2e1cdb70> None
<__main__.newNode object at 0x7f2b2e1cdcf8> None True <__main__.newNode object at 0x7f2b2e1cdba8> 0
<__main__.newNode object at 0x7f2b2e1cdb70> 178 False <__main__.newNode object at 0x7f2b2e1c

<__main__.newNode object at 0x7f2b31ccdeb8> 165 False <__main__.newNode object at 0x7f2b31ce7c88> None
<__main__.newNode object at 0x7f2b31ccdc88> None True <__main__.newNode object at 0x7f2b31ccdeb8> 0
<__main__.newNode object at 0x7f2b2dd66a20> 186 False <__main__.newNode object at 0x7f2b2dd669e8> None
<__main__.newNode object at 0x7f2b31ccdac8> 109 True <__main__.newNode object at 0x7f2b31ccda20> 0
<__main__.newNode object at 0x7f2b31ccda20> 27 False <__main__.newNode object at 0x7f2b31ccda58> None
<__main__.newNode object at 0x7f2b31ccd908> 20 True <__main__.newNode object at 0x7f2b31ccda20> 1
<__main__.newNode object at 0x7f2b31ccda58> 66 False <__main__.newNode object at 0x7f2b31ccdcc0> None
<__main__.newNode object at 0x7f2b31ccd7b8> None True <__main__.newNode object at 0x7f2b31ccda58> 1
<__main__.newNode object at 0x7f2b31ccdcc0> 391 False <__main__.newNode object at 0x7f2b31ccdba8> None
<__main__.newNode object at 0x7f2b31ccdd68> 20 True <__main__.newNode object at 0x7f2b31cc

<__main__.newNode object at 0x7f2b3146f390> 2 True <__main__.newNode object at 0x7f2b31467390> 0
<__main__.newNode object at 0x7f2b31467358> 79 False <__main__.newNode object at 0x7f2b31467320> None
<__main__.newNode object at 0x7f2b3146f470> None True <__main__.newNode object at 0x7f2b3146f438> 0
<__main__.newNode object at 0x7f2b3146f438> 20 False <__main__.newNode object at 0x7f2b31467358> None
<__main__.newNode object at 0x7f2b3146f4e0> None True <__main__.newNode object at 0x7f2b3146f4a8> 0
<__main__.newNode object at 0x7f2b3146f4a8> 20 False <__main__.newNode object at 0x7f2b3146f438> None
<__main__.newNode object at 0x7f2b3146f550> 20 True <__main__.newNode object at 0x7f2b3146f518> 0
<__main__.newNode object at 0x7f2b3146f518> 20 False <__main__.newNode object at 0x7f2b3146f4a8> None
<__main__.newNode object at 0x7f2b3146f5f8> None True <__main__.newNode object at 0x7f2b3146f518> 0
<__main__.newNode object at 0x7f2b31467320> 105 False <__main__.newNode object at 0x7f2b314672e8>

...

<__main__.newNode object at 0x7f2b32115d68> 19 False <__main__.newNode object at 0x7f2b32115d30> None
<__main__.newNode object at 0x7f2b321357f0> 19 True <__main__.newNode object at 0x7f2b32115d68> 0
<__main__.newNode object at 0x7f2b32115d30> 245 False <__main__.newNode object at 0x7f2b32115cf8> None
<__main__.newNode object at 0x7f2b32135828> None True <__main__.newNode object at 0x7f2b32115d30> 1
<__main__.newNode object at 0x7f2b32115cf8> 151 False <__main__.newNode object at 0x7f2b32115cc0> None
<__main__.newNode object at 0x7f2b321355c0> None True <__main__.newNode object at 0x7f2b321355f8> 0
<__main__.newNode object at 0x7f2b321355f8> 151 False <__main__.newNode object at 0x7f2b32135898> None
<__main__.newNode object at 0x7f2b32135630> 80 True <__main__.newNode object at 0x7f2b32135668> 0
<__main__.newNode object at 0x7f2b32135668> 151 False <__main__.newNode object at 0x7f2b321355f8> None
<__main__.newNode object at 0x7f2b321354e0> None True <__main__.newNode object at 0x7f2b32

<__main__.newNode object at 0x7f2b31e9a4a8> 209 False <__main__.newNode object at 0x7f2b31e9a438> None
<__main__.newNode object at 0x7f2b31e9a588> None True <__main__.newNode object at 0x7f2b31e9a4a8> 0
<__main__.newNode object at 0x7f2b31e9a400> 151 False <__main__.newNode object at 0x7f2b31e9a1d0> None
<__main__.newNode object at 0x7f2b31e9a5c0> 209 True <__main__.newNode object at 0x7f2b31e9a400> 0
<__main__.newNode object at 0x7f2b31e99f28> 8 False <__main__.newNode object at 0x7f2b31e99ef0> None
<__main__.newNode object at 0x7f2b31e9a668> None True <__main__.newNode object at 0x7f2b31e99f28> 0
<__main__.newNode object at 0x7f2b31e99ef0> 5 False <__main__.newNode object at 0x7f2b31e99eb8> None
<__main__.newNode object at 0x7f2b31e9a6d8> 19 True <__main__.newNode object at 0x7f2b31e9a6a0> 1
<__main__.newNode object at 0x7f2b31e9a6a0> 27 False <__main__.newNode object at 0x7f2b31e99ef0> None
<__main__.newNode object at 0x7f2b31e9a780> None True <__main__.newNode object at 0x7f2b31e9a

<__main__.newNode object at 0x7f2b3138f1d0> 151 False <__main__.newNode object at 0x7f2b3138f0f0> None
<__main__.newNode object at 0x7f2b3138f240> 209 True <__main__.newNode object at 0x7f2b3138f1d0> 0
<__main__.newNode object at 0x7f2b316cbf28> 19 False <__main__.newNode object at 0x7f2b316cbef0> None
<__main__.newNode object at 0x7f2b3138f2e8> None True <__main__.newNode object at 0x7f2b316cbf28> 1
<__main__.newNode object at 0x7f2b316cbef0> 151 False <__main__.newNode object at 0x7f2b316cbeb8> None
<__main__.newNode object at 0x7f2b3138f3c8> 151 True <__main__.newNode object at 0x7f2b3138f390> 0
<__main__.newNode object at 0x7f2b3138f390> 151 False <__main__.newNode object at 0x7f2b3138f358> None
<__main__.newNode object at 0x7f2b3138f4a8> 151 True <__main__.newNode object at 0x7f2b3138f470> 0
<__main__.newNode object at 0x7f2b3138f470> 151 False <__main__.newNode object at 0x7f2b3138f390> None
<__main__.newNode object at 0x7f2b3138f550> None True <__main__.newNode object at 0x7f2b3

<__main__.newNode object at 0x7f2b318eac50> 36 False <__main__.newNode object at 0x7f2b318eac18> None
<__main__.newNode object at 0x7f2b318eaf60> None True <__main__.newNode object at 0x7f2b318eac50> 0
<__main__.newNode object at 0x7f2b318eac18> 81 False <__main__.newNode object at 0x7f2b318eabe0> None
<__main__.newNode object at 0x7f2b318eaf98> None True <__main__.newNode object at 0x7f2b318eac18> 0
<__main__.newNode object at 0x7f2b318eabe0> 160 False <__main__.newNode object at 0x7f2b318eaba8> None
<__main__.newNode object at 0x7f2b318eafd0> 112 True <__main__.newNode object at 0x7f2b318eabe0> 1
<__main__.newNode object at 0x7f2b318eaba8> 233 False <__main__.newNode object at 0x7f2b318eab70> None
<__main__.newNode object at 0x7f2b318c10f0> 112 True <__main__.newNode object at 0x7f2b318c10b8> 0
<__main__.newNode object at 0x7f2b318c10b8> 129 False <__main__.newNode object at 0x7f2b318eaba8> None
<__main__.newNode object at 0x7f2b318c11d0> 153 True <__main__.newNode object at 0x7f2b31

<__main__.newNode object at 0x7f2b310299b0> 20 False <__main__.newNode object at 0x7f2b30f53860> None
<__main__.newNode object at 0x7f2b31029d30> 20 True <__main__.newNode object at 0x7f2b31029cf8> 0
<__main__.newNode object at 0x7f2b31029cf8> 20 False <__main__.newNode object at 0x7f2b31029cc0> None
<__main__.newNode object at 0x7f2b31029dd8> None True <__main__.newNode object at 0x7f2b31029cf8> 0
<__main__.newNode object at 0x7f2b31029cc0> 34 False <__main__.newNode object at 0x7f2b31029c88> None
<__main__.newNode object at 0x7f2b31029e10> 209 True <__main__.newNode object at 0x7f2b31029cc0> 1
<__main__.newNode object at 0x7f2b31029c88> 138 False <__main__.newNode object at 0x7f2b31029c50> None
<__main__.newNode object at 0x7f2b31029eb8> None True <__main__.newNode object at 0x7f2b31029c88> 1
<__main__.newNode object at 0x7f2b31029c50> 209 False <__main__.newNode object at 0x7f2b31029c18> None
<__main__.newNode object at 0x7f2b31029f28> None True <__main__.newNode object at 0x7f2b310

In [30]:
train_acc, val_acc, test_acc = root.tree.calc_accuracy(X_train.A, train_class, X_valid.A, valid_class, X_test.A, test_class)

In [31]:
print("--------------Pruned all Leaves from Tree------------------------------\n")
print("Number of Nodes = ", n)
print("The Training Accuracy on Full-Grown Tree is = {:2.3f}%".format(train_acc*100))
print("The Vaidation Accuracy on Full-Grown Tree is = {:2.3f}%".format(val_acc*100))
print("The Test Accuracy on Full-Grown Tree is = {:2.3f}%".format(test_acc*100))

--------------Pruned all Leaves from Tree------------------------------

Number of Nodes =  14913
The Training Accuracy on Full-Grown Tree is = 85.805%
The Vaidation Accuracy on Full-Grown Tree is = 77.100%
The Test Accuracy on Full-Grown Tree is = 77.451%


In [ ]:
# Traverse Tree with different Depth

In [135]:
def traverse(graph, depth):
    global dep
    node = graph
    
    while (node.left is not None):
        node = node.left
        dep+=1
        if (dep == depth):
            
    global n
    if graph:
        n+=1
        # First recur on left child 
        printInorder(graph.left) 
        # then print the data of node 
        print(graph.attribute, graph.value, graph.parent) 
  
        # now recur on right child 
        printInorder(graph.right)
        


In [136]:
n = 0
dep = 0
traverse(root.tree, 5)
print(n)

None True <__main__.newNode object at 0x7f9bf099c3c8>
22 False <__main__.newNode object at 0x7f9bf099c390>
None True <__main__.newNode object at 0x7f9bf099c3c8>
104 False <__main__.newNode object at 0x7f9bf099c358>
None True <__main__.newNode object at 0x7f9bf099c390>
20 False <__main__.newNode object at 0x7f9bf099c320>
None True <__main__.newNode object at 0x7f9bf099c630>
20 False <__main__.newNode object at 0x7f9bf099c358>
None True <__main__.newNode object at 0x7f9bf099c6d8>
20 False <__main__.newNode object at 0x7f9bf099c6a0>
None True <__main__.newNode object at 0x7f9bf099c6d8>
20 False <__main__.newNode object at 0x7f9bf099c630>
None True <__main__.newNode object at 0x7f9bf099c6a0>
32 False <__main__.newNode object at 0x7f9bf099c2e8>
None True <__main__.newNode object at 0x7f9bf099c320>
36 False <__main__.newNode object at 0x7f9bf099c2b0>
None True <__main__.newNode object at 0x7f9bf099c7f0>
87 False <__main__.newNode object at 0x7f9bf099c2e8>
None True <__main__.newNode object a

203 False <__main__.newNode object at 0x7f9bf23722b0>
None True <__main__.newNode object at 0x7f9bf23723c8>
84 False <__main__.newNode object at 0x7f9bf23722e8>
None True <__main__.newNode object at 0x7f9bf23723c8>
107 False <__main__.newNode object at 0x7f9bf3fecda0>
None True <__main__.newNode object at 0x7f9bf2372470>
151 False <__main__.newNode object at 0x7f9bf23722b0>
None True <__main__.newNode object at 0x7f9bf2372518>
151 False <__main__.newNode object at 0x7f9bf23724e0>
None True <__main__.newNode object at 0x7f9bf2372518>
151 False <__main__.newNode object at 0x7f9bf2372470>
None True <__main__.newNode object at 0x7f9bf23724e0>
363 False <__main__.newNode object at 0x7f9bf3fecd30>
None True <__main__.newNode object at 0x7f9bf3fecd68>
100 False <__main__.newNode object at 0x7f9bf3fef8d0>
None True <__main__.newNode object at 0x7f9bf3fecd30>
93 False <__main__.newNode object at 0x7f9bf3fef860>
None True <__main__.newNode object at 0x7f9bf23726a0>
198 False <__main__.newNode ob

106 False <__main__.newNode object at 0x7f9bf4210048>
None True <__main__.newNode object at 0x7f9bf4210080>
368 False <__main__.newNode object at 0x7f9bf4008fd0>
None True <__main__.newNode object at 0x7f9bf4210978>
32 False <__main__.newNode object at 0x7f9bf4210048>
None True <__main__.newNode object at 0x7f9bf4210978>
359 False <__main__.newNode object at 0x7f9bf4008f98>
None True <__main__.newNode object at 0x7f9bf4210cc0>
190 False <__main__.newNode object at 0x7f9bf4210c88>
None True <__main__.newNode object at 0x7f9bf4210d30>
0 False <__main__.newNode object at 0x7f9bf4210cc0>
None True <__main__.newNode object at 0x7f9bf4210d30>
209 False <__main__.newNode object at 0x7f9bf4210c50>
None True <__main__.newNode object at 0x7f9bf4210eb8>
100 False <__main__.newNode object at 0x7f9bf4210e80>
None True <__main__.newNode object at 0x7f9bf4210eb8>
36 False <__main__.newNode object at 0x7f9bf4210e48>
None True <__main__.newNode object at 0x7f9bf4210e80>
23 False <__main__.newNode objec

None True <__main__.newNode object at 0x7f9bf3943080>
25 False <__main__.newNode object at 0x7f9bf07c38d0>
None True <__main__.newNode object at 0x7f9bf3943080>
68 False <__main__.newNode object at 0x7f9bf07c3860>
None True <__main__.newNode object at 0x7f9bf07c3898>
20 False <__main__.newNode object at 0x7f9bf50be320>
None True <__main__.newNode object at 0x7f9bf07c3860>
240 False <__main__.newNode object at 0x7f9bf50be2b0>
None True <__main__.newNode object at 0x7f9bf3943438>
19 False <__main__.newNode object at 0x7f9bf3943400>
None True <__main__.newNode object at 0x7f9bf39434a8>
391 False <__main__.newNode object at 0x7f9bf3943438>
None True <__main__.newNode object at 0x7f9bf39434a8>
115 False <__main__.newNode object at 0x7f9bf39433c8>
None True <__main__.newNode object at 0x7f9bf3943588>
19 False <__main__.newNode object at 0x7f9bf3943550>
None True <__main__.newNode object at 0x7f9bf3943588>
107 False <__main__.newNode object at 0x7f9bf3943400>
None True <__main__.newNode objec

None True <__main__.newNode object at 0x7f9bf39ebf28>
67 False <__main__.newNode object at 0x7f9bf39ebeb8>
None True <__main__.newNode object at 0x7f9bf39ebfd0>
80 False <__main__.newNode object at 0x7f9bf39ebef0>
None True <__main__.newNode object at 0x7f9bf39ebfd0>
20 False <__main__.newNode object at 0x7f9bf39ebe80>
None True <__main__.newNode object at 0x7f9bf39ebeb8>
210 False <__main__.newNode object at 0x7f9bf39ebe48>
None True <__main__.newNode object at 0x7f9bf40540f0>
80 False <__main__.newNode object at 0x7f9bf39ebe80>
None True <__main__.newNode object at 0x7f9bf4054160>
67 False <__main__.newNode object at 0x7f9bf40540f0>
None True <__main__.newNode object at 0x7f9bf4054160>
19 False <__main__.newNode object at 0x7f9bf39ebe10>
None True <__main__.newNode object at 0x7f9bf39ebe48>
107 False <__main__.newNode object at 0x7f9bf39ebdd8>
None True <__main__.newNode object at 0x7f9bf39ebe10>
36 False <__main__.newNode object at 0x7f9bf39eb4a8>
None True <__main__.newNode object 

...

151 False <__main__.newNode object at 0x7f9bf2623c50>
None True <__main__.newNode object at 0x7f9bf2623d68>
138 False <__main__.newNode object at 0x7f9bf2623d30>
None True <__main__.newNode object at 0x7f9bf2623d68>
151 False <__main__.newNode object at 0x7f9bf2623cf8>
None True <__main__.newNode object at 0x7f9bf2623d30>
151 False <__main__.newNode object at 0x7f9bf2623c88>
None True <__main__.newNode object at 0x7f9bf2623cf8>
115 False <__main__.newNode object at 0x7f9bf2623c18>
None True <__main__.newNode object at 0x7f9bf2623e80>
71 False <__main__.newNode object at 0x7f9bf2623c50>
None True <__main__.newNode object at 0x7f9bf2623e80>
90 False <__main__.newNode object at 0x7f9bf2623be0>
None True <__main__.newNode object at 0x7f9bf2623f60>
151 False <__main__.newNode object at 0x7f9bf2623f28>
None True <__main__.newNode object at 0x7f9bf2623f60>
151 False <__main__.newNode object at 0x7f9bf2623c18>
None True <__main__.newNode object at 0x7f9bf2623f28>
2 False <__main__.newNode obje

209 False <__main__.newNode object at 0x7f9bf24c4b38>
None True <__main__.newNode object at 0x7f9bf24c4b70>
209 False <__main__.newNode object at 0x7f9bf24c4b00>
None True <__main__.newNode object at 0x7f9bf24c4b38>
209 False <__main__.newNode object at 0x7f9bf24c4ac8>
None True <__main__.newNode object at 0x7f9bf24c4c88>
151 False <__main__.newNode object at 0x7f9bf24c4c50>
None True <__main__.newNode object at 0x7f9bf24c4c88>
151 False <__main__.newNode object at 0x7f9bf24c4b00>
None True <__main__.newNode object at 0x7f9bf24c4c50>
209 False <__main__.newNode object at 0x7f9bf24c4a90>
None True <__main__.newNode object at 0x7f9bf24c4ac8>
87 False <__main__.newNode object at 0x7f9bf24c4a58>
None True <__main__.newNode object at 0x7f9bf24c4a90>
19 False <__main__.newNode object at 0x7f9bf24c4198>
None True <__main__.newNode object at 0x7f9bf24c4a58>
24 False <__main__.newNode object at 0x7f9bf24c6a90>
None True <__main__.newNode object at 0x7f9bf24c4e80>
151 False <__main__.newNode obj

None True <__main__.newNode object at 0x7f9bf4d5a780>
209 False <__main__.newNode object at 0x7f9bf4d5a5f8>
None True <__main__.newNode object at 0x7f9bf4d5a6d8>
19 False <__main__.newNode object at 0x7f9bf4d5a588>
None True <__main__.newNode object at 0x7f9bf4d5a5c0>
198 False <__main__.newNode object at 0x7f9bf4d5a550>
None True <__main__.newNode object at 0x7f9bf4d5a588>
80 False <__main__.newNode object at 0x7f9bf4d5a518>
None True <__main__.newNode object at 0x7f9bf4d5a550>
52 False <__main__.newNode object at 0x7f9bf4d5a4e0>
None True <__main__.newNode object at 0x7f9bf4d5a978>
209 False <__main__.newNode object at 0x7f9bf4d5a518>
None True <__main__.newNode object at 0x7f9bf4d5a978>
34 False <__main__.newNode object at 0x7f9bf4d5a4a8>
None True <__main__.newNode object at 0x7f9bf4d5aa90>
80 False <__main__.newNode object at 0x7f9bf4d5aa58>
None True <__main__.newNode object at 0x7f9bf4d5aa90>
151 False <__main__.newNode object at 0x7f9bf4d5aa20>
None True <__main__.newNode objec

None True <__main__.newNode object at 0x7f9bf25da438>
27 False <__main__.newNode object at 0x7f9bf25da400>
None True <__main__.newNode object at 0x7f9bf25da438>
19 False <__main__.newNode object at 0x7f9bf25da390>
None True <__main__.newNode object at 0x7f9bf25da400>
84 False <__main__.newNode object at 0x7f9bf26f8ba8>
None True <__main__.newNode object at 0x7f9bf25da5f8>
141 False <__main__.newNode object at 0x7f9bf25da5c0>
None True <__main__.newNode object at 0x7f9bf25da5f8>
34 False <__main__.newNode object at 0x7f9bf25da588>
None True <__main__.newNode object at 0x7f9bf25da5c0>
115 False <__main__.newNode object at 0x7f9bf25da550>
None True <__main__.newNode object at 0x7f9bf25da588>
90 False <__main__.newNode object at 0x7f9bf25da518>
None True <__main__.newNode object at 0x7f9bf25da550>
84 False <__main__.newNode object at 0x7f9bf25da358>
None True <__main__.newNode object at 0x7f9bf25da518>
154 False <__main__.newNode object at 0x7f9bf242af60>
None True <__main__.newNode object

None True <__main__.newNode object at 0x7f9bf24471d0>
20 False <__main__.newNode object at 0x7f9bf2447198>
None True <__main__.newNode object at 0x7f9bf2447240>
20 False <__main__.newNode object at 0x7f9bf24471d0>
None True <__main__.newNode object at 0x7f9bf2447240>
15 False <__main__.newNode object at 0x7f9bf2447048>
None True <__main__.newNode object at 0x7f9bf2447198>
24 False <__main__.newNode object at 0x7f9bf245ff98>
None True <__main__.newNode object at 0x7f9bf245ffd0>
209 False <__main__.newNode object at 0x7f9bf245ff60>
None True <__main__.newNode object at 0x7f9bf2447438>
20 False <__main__.newNode object at 0x7f9bf2447400>
None True <__main__.newNode object at 0x7f9bf2447438>
20 False <__main__.newNode object at 0x7f9bf24473c8>
None True <__main__.newNode object at 0x7f9bf2447400>
64 False <__main__.newNode object at 0x7f9bf2447390>
None True <__main__.newNode object at 0x7f9bf24473c8>
27 False <__main__.newNode object at 0x7f9bf2447358>
None True <__main__.newNode object a

In [ ]:
def predict(tree, data):
    if tree.leaf:
        return tree.final
    if tree.left is None and tree.right is None:
        if tree.value[0] > tree.value[1]:
            return 0
        else:
            return 1
    if data[tree.attribute] <= tree.threshold:
        return predict(tree.left, data)
    elif data[tree.attribute] > tree.threshold:
        return predict(tree.right, data)